## Schooling and fertility

Here we are analyzing this dataset from the World Bank on gender and
inequality:

* [https://data.worldbank.org/data-catalog/gender-statistics](https://data.worldbank.org/data-catalog/gender-statistics)

You can download the data yourself as a zip file [from that site](http://databank.worldbank.org/data/download/Gender_Stats_csv.zip), but to
make your life a little easier, I’ve made a link to the extracted data file:

* [Gender_StatsData.csv](https://matthew-brett.github.io/les-pilot/_downloads/Gender_StatsData.csv)

Download this file to the same directory as your Jupyter Notebook.

In [ ]:
# Import Pandas with its usual short name
import pandas as pd

Load the Comma Separated Value text file into Pandas as a data frame:

In [ ]:
df = pd.read_csv('Gender_StatsData.csv')

This is a slightly clumsy-looking data frame, because it has years for
columns, and variables for rows, where there are 630 variables for each
country.  So there are 630 rows \* the number of countries.  To investigate, we
first look at the column names:

In [ ]:
df.columns

Next we look at the data frame itself:

In [ ]:
df

There are lots of countries here, so to start, let’s look at the variables for
the UK.

We get the UK country code from [http://www.worldatlas.com/aatlas/ctycodes.htm](http://www.worldatlas.com/aatlas/ctycodes.htm).
The code is `GBR`.

In [ ]:
# We select only the UK rows
gb = df[df['Country Code'] == 'GBR']
gb

Pandas truncates the output to only show a certain number of rows, and only a
certain length for the text fields.  To investigate further, you can increase
these limits to see all 630 rows for the UK, and more of the text for the text
fields:

In [ ]:
# See more of the text, more rows in the displayed output
pd.options.display.max_colwidth = 80
pd.options.display.max_rows = 700

If you are working in the Notebook, you will now see all of the rows and the
whole text field with the variable description.

In [ ]:
# This will be different from above when working in the Notebook
gb

After scanning through this output, we decide we want to look at these two
variables:

* `SP.ADO.TFRT` : Adolescent fertility rate (births per 1,000 women ages
  15-19)

* `SE.SCH.LIFE.FE` : Expected years of schooling, female

Remember that, for each variable there is one row per country.  We have to
select the rows corresponding to this variable, for all countries.  We do that
for both variables we are interested in.

In [ ]:
# Put the variables we want into their own data frames
fertility_rate = df[df['Indicator Code'] == 'SP.ADO.TFRT']
age_female_sch = df[df['Indicator Code'] == 'SE.SCH.LIFE.FE']

For convenience, we are going to put the values from these columns back into
their own data frame.  To do that, we make a new data frame, and fill it with
the values from our variables:

In [ ]:
# Make a new data frame to store our school and fertility columns
school_fertility = pd.DataFrame(columns=['school', 'fertility'])
school_fertility

We fill the empty data frame with the values we selected:

In [ ]:
school_fertility['school'] = age_female_sch['2014'].values
school_fertility['fertility'] = fertility_rate['2014'].values
school_fertility

We do not have the expected length of schooling for quite a few contries;
these are the rows with `NaN` in the corresponding columns.  “NaN” stands
for Not a Number. We often call these *missing values*. They can also be
called “NA” for “Not Applicable”.  There are some missing values for the
fertility statistic too.  For simplicity, we drop rows that have missing
values in either of these two columns:

In [ ]:
# Drop the rows with any missing (NaN) values
school_fertility = school_fertility.dropna()
school_fertility

Now we have the data we think we want, we do a quick check for odd values by
doing a histogram of each column:

In [ ]:
%matplotlib inline

In [ ]:
# Import the plotting library with a memorable name
import matplotlib.pyplot as plt

In [ ]:
# Histogram of the school length
plt.hist(school_fertility['school']);

In [ ]:
# Histogram of the fertility rate
plt.hist(school_fertility['fertility']);

Now to the part we are interested in.  We speculate that countries that don’t
keep their women in school for long, may have higher adolescent fertility
rates.  We plot length of schooling on the X axis and fertility rates on the Y
axis:

In [ ]:
# Scatterplot of school length against fertility rate
plt.scatter(school_fertility['school'], school_fertility['fertility'])

We save the data frame we made to a file, so we can use these values again.
When saving, we drop off the first implicit column, with the case numbers:

In [ ]:
school_fertility.to_csv('school_fertility.csv', index=False)

As usual, we make lists for our two sets of numbers:

In [ ]:
school = list(school_fertility['school'])
fertility = list(school_fertility['fertility'])

We have speculated that, as the number of years in school goes up, the number
of adolescents having children goes down.

Remember [What order is best?](https://matthew-brett.github.io/les-pilot/what_order_is_best.html)?  If `school` and `fertility` are
perfectly arranged, with low values for `school` going with high values of
`fertility`, we will get a high `list_product`:

In [ ]:
def list_product(first_list, second_list):
    product = 0
    for i in range(len(first_list)):
        value = first_list[i] * second_list[i]
        product = product + value
    return product

So, what do we get for our observed lists?

In [ ]:
observed_product = list_product(school, fertility)

What do we compare this to?  What is our sampling distribution?

We need our null hypothesis again.

Our null hypothesis is that there is no systematic shared ordering to
`school` and `fertility`.  Any appearance of shared ordering is just
because of random sampling variation in `school` and `fertility`.

We can get an idea of sampling variation by doing something very similar to
what we did in [Comparing two groups with permutation testing](https://matthew-brett.github.io/les-pilot/brexit_ages.html).  We can permute the `fertility` list to
give a random sample of fertility values.  So, here is one trial:

In [ ]:
#: The random module
import random

In [ ]:
def one_product(list_1, list_2):
    # We don't want to change list_2, so make a copy
    new_list_2 = list_2.copy()
    random.shuffle(new_list_2)
    return list_product(list_1, new_list_2)

In [ ]:
one_product(school, fertility)

In [ ]:
one_product(school, fertility)

Now let’s build up the sampling distribution:

In [ ]:
n_repeats = 10000
sample_products = []
for i in range(n_repeats):
    product = one_product(school, fertility)
    sample_products.append(product)

In [ ]:
plt.hist(sample_products)